<a href="https://colab.research.google.com/github/Sovanno/NLP/blob/main/LAB2_B.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import requests

In [ ]:
def fetch_vacancies(keyword, per_page=100):
    url = "https://api.hh.ru/vacancies"
    vacancies = []
    page = 0

    while True:
        params = {
            'text': keyword,
            'area': "1",  # Москва
            'per_page': per_page,
            'page': page
        }

        response = requests.get(url, params=params)
        if response.status_code != 200:
            print(f"Ошибка: {response.status_code}")
            break

        data = response.json()
        vacancies.extend(data.get('items', []))

        if page >= data['pages'] - 1:
            break
        page += 1

        if len(vacancies) >= 200:
            break

    return vacancies[:200]

In [ ]:
keyword = "Data Scientist"
raw_vacancies = fetch_vacancies(keyword)

In [ ]:
print(len(raw_vacancies))

200


In [ ]:
from concurrent.futures import ThreadPoolExecutor
from tqdm import tqdm

In [ ]:
def fetch_vacancy_details(vacancy_id):
    url = f"https://api.hh.ru/vacancies/{vacancy_id}"
    response = requests.get(url)
    if response.status_code == 200:
        return response.json()
    else:
        return None

In [ ]:
def fetch_all_details(vacancies):
    vacancy_ids = [v['id'] for v in vacancies]
    details = []

    with ThreadPoolExecutor() as executor:
        results = list(tqdm(executor.map(fetch_vacancy_details, vacancy_ids), total=len(vacancy_ids)))
        details.extend(filter(None, results))

    return details

In [ ]:
vacancy_details1 = fetch_all_details(raw_vacancies[:100])

100%|██████████| 100/100 [00:11<00:00,  8.52it/s]


In [ ]:
vacancy_details2 = fetch_all_details(raw_vacancies[100:])

100%|██████████| 100/100 [00:11<00:00,  8.58it/s]


In [ ]:
vacancy_details1.extend(vacancy_details2)

In [ ]:
vacancy_details = vacancy_details1

In [ ]:
print(len(vacancy_details))

200


In [ ]:
print(vacancy_details)

[{'id': '110079483', 'premium': False, 'billing_type': {'id': 'standard', 'name': 'Стандарт'}, 'relations': [], 'name': 'Data Scientist', 'insider_interview': None, 'response_letter_required': False, 'area': {'id': '1', 'name': 'Москва', 'url': 'https://api.hh.ru/areas/1'}, 'salary': None, 'type': {'id': 'open', 'name': 'Открытая'}, 'address': None, 'allow_messages': True, 'experience': {'id': 'noExperience', 'name': 'Нет опыта'}, 'schedule': {'id': 'remote', 'name': 'Удаленная работа'}, 'employment': {'id': 'full', 'name': 'Полная занятость'}, 'department': None, 'contacts': None, 'description': '<strong>Обязанности:</strong> <ul> <li>\u200b\u200b\u200b\u200b\u200b\u200b\u200bРазработка и оптимизация моделей кредитного скоринга для оценки кредитоспособности заемщиков</li> <li>Анализ и обработка больших объемов данных с целью выявления закономерностей и зависимостей</li> <li>Анализ дополнительных источников данных для включения в скоринговые модели</li> <li>Оценка эффективности разрабо

In [ ]:
print(raw_vacancies)

[{'id': '110079483', 'premium': False, 'name': 'Data Scientist', 'department': None, 'has_test': False, 'response_letter_required': False, 'area': {'id': '1', 'name': 'Москва', 'url': 'https://api.hh.ru/areas/1'}, 'salary': None, 'type': {'id': 'open', 'name': 'Открытая'}, 'address': None, 'response_url': None, 'sort_point_distance': None, 'published_at': '2024-11-04T22:42:55+0300', 'created_at': '2024-11-04T22:42:55+0300', 'archived': False, 'apply_alternate_url': 'https://hh.ru/applicant/vacancy_response?vacancyId=110079483', 'show_logo_in_search': None, 'insider_interview': None, 'url': 'https://api.hh.ru/vacancies/110079483?host=hh.ru', 'alternate_url': 'https://hh.ru/vacancy/110079483', 'relations': [], 'employer': {'id': '913808', 'name': 'CarMoney', 'url': 'https://api.hh.ru/employers/913808', 'alternate_url': 'https://hh.ru/employer/913808', 'logo_urls': {'240': 'https://img.hhcdn.ru/employer-logo/1685479.jpeg', 'original': 'https://img.hhcdn.ru/employer-logo-original/310778.jp

In [ ]:
print(len(vacancy_details))

120


In [ ]:
import re
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer
from nltk.corpus import stopwords

In [ ]:
def preprocess_text(text):
    # Очистка от HTML-тегов и специальных символов
    text = re.sub(r'<[^>]+>', '', text)
    text = re.sub(r'[^\w\s]', '', text)

    # Токенизация
    tokens = word_tokenize(text.lower())

    # Удаление стоп-слов
    stop_words = set(stopwords.words('russian') + stopwords.words('english'))
    tokens = [word for word in tokens if word not in stop_words]

    # Лемматизация
    lemmatizer = WordNetLemmatizer()
    tokens = [lemmatizer.lemmatize(token) for token in tokens]

    return tokens

In [ ]:
def preprocess_vacancies(vacancies):
    processed_vacancies = []
    for vacancy in tqdm(vacancies):
        description = vacancy.get('description', '')
        tokens = preprocess_text(description)
        processed_vacancies.append(tokens)
    return processed_vacancies

In [ ]:
import nltk
nltk.download('punkt_tab')
nltk.download('stopwords')
nltk.download('wordnet')

[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...


True

In [ ]:
processed_data = preprocess_vacancies(vacancy_details)

100%|██████████| 200/200 [00:04<00:00, 44.06it/s] 


In [ ]:
print(processed_data)
print(len(processed_data))

[['наша', 'команда', 'занимается', 'моделированием', 'прогнозированием', 'утилизации', 'серверного', 'парка', 'ozon', 'помогаем', 'масштабировать', 'quotжелезныеquot', 'ресурсы', 'ozon', 'быструю', 'экспансии', 'компании', 'российский', 'международный', 'рынки', 'основными', 'фокусами', 'являются', 'моделирование', 'скорости', 'роста', 'серверного', 'парка', 'зависимости', 'стратегии', 'экспансии', 'бизнеса', 'прогнозирование', 'потреблений', 'quotжелезныхquot', 'ресурсов', 'rps', 'cpu', 'ram', 'периоды', 'распродаж', 'расчет', 'капитальных', 'операционных', 'бюджетов', 'инфраструктуры', 'data', 'scientist', 'это', 'сотрудник', 'широкого', 'профиля', 'который', 'занимается', 'классическими', 'mlзадачами', 'временные', 'ряды', 'математическая', 'оптимизация', 'разработкой', 'mlсервисов', 'облаке', 'ozon', 'аналитической', 'поддержкой', 'бизнеса', 'созданием', 'дэшбордов', 'etlпайплайнов', 'аналитических', 'отчётов', 'тебе', 'предстоит', 'обнаружение', 'интерпритация', 'значимых', 'закон

In [ ]:
import pickle

In [ ]:
def save_to_pickle(data, filename):
    with open(filename, 'wb') as f:
        pickle.dump(data, f)

In [ ]:
output_file = "vacancies_tokens.pkl"
save_to_pickle(processed_data, output_file)

In [ ]:
from google.colab import drive

In [ ]:
drive.mount('/content/drive')
output_file = "/content/drive/My Drive/vacancies_tokens.pkl"

Mounted at /content/drive
